# Code

### Imports

In [15]:
import inseq
import pandas as pd
import warnings
import byt5_model
import torch

warnings.filterwarnings("ignore")

### Functions

In [16]:
class InseqAttributer:
    def __init__(self, model="./models/test/", attribution_method="input_x_gradient") -> None:
        """Create an object that loads a given model through Inseq with a given attribution method"""
        self.model = inseq.load_model(model, attribution_method)
    
    def attribute(self, inp:str, out:str=None):
        """Use the Inseq model to generate feature attributions using a given input or input & output"""
        if inp and out:
            inp_out = (inp, out)
        else:
            inp_out = (inp,)

        inseq_out = self.model.attribute(*inp_out,
                                         attribute_target=True,
                                         step_scores=["probability"])
        inseq_out.show()

In [17]:
def data_sampler(data, model, samples=10, spaces=True, device='auto'):

    if device == 'auto':
        device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")
    elif device == 'gpu' or device == 'cuda':
        device = torch.device("cuda")
    elif device == 'cpu':
        device = torch.device("cpu")
    else:
        print('Set device to auto, cpu, or gpu/cuda.')
        return

    test = pd.read_csv(
        data,
        sep='\t',
        names=('lemma', 'labels', 'features')
    )

    if spaces:
        test['inputs'] = test['lemma'] + ' ' + test['features']
    else:
        test['inputs'] = test['lemma'] + test['features']


    test_gen_comparison = byt5_model.comparer(test, byt5_model.generate(model, test, device), show_output=False)
    test = pd.concat([test, test_gen_comparison], axis=1).rename(columns={'labels': 'plural'})

    correct = []
    for idx, row in test.iterrows():
        if row['Expected'] == row['Predicted']:
            correct.append('correct')
        else:
            correct.append('incorrect')

    test = test.assign(correct=correct)

    return pd.concat([test[test.correct == 'incorrect'].sample(n=samples//2, random_state=1234),
                      test[test.correct == 'correct'].sample(n=samples//2, random_state=1234)])

In [18]:
def sample_runner(samples, inseq_model, expected=False):
    count = 0
    for idx, sample in samples.iterrows():
        count += 1
        if count > 1:
            print('\n')
        print('='*80)

        inp = sample['lemma'] + ' ' + sample['features']
        if expected:
            print('Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)')
            output_type = 'gold'
            out = sample['Expected']
        else:
            print('Testing Predicted (pred) outcome (what did the model take from the input during generation)')
            output_type = 'pred'
            out = sample['Predicted']

        print('Sample: {}\nIndex: {}\nThis prediction is {}\nInput -> output ({}): \'{}\' -> \'{}\''.format(
             count, idx, sample['correct'], output_type, inp, out
        ))
        if output_type == 'pred':
            print(f"The expected or gold output would be '{sample['Expected']}'")

        print('='*80)

        inseq_model.attribute(inp,
                              out)

# Testing

## German

### Setup

In [19]:
model_ger_finetuned = "./models/finetuned_ger"
inseq_ger_finetuned = InseqAttributer(model_ger_finetuned, "input_x_gradient")

In [20]:
model_ger_fromscratch = "./models/saved_model_scratch_ger_new"
inseq_ger_fromscratch = InseqAttributer(model_ger_fromscratch, "input_x_gradient")

### German Finetuned

The sample_runner function splits the given amount of samples in `two` (default is 10) so that `~50% of the samples are samples of correct predictions`, and `~50% of the samples are samples of incorrect predictions`.

First the incorrect predictions are shown, then the correct ones are shown (in the outcomes below, this translates to `5 incorrect items or 1-5, followed by 5 correct items or 6-10`).

In [21]:
sample_runner(data_sampler('./data/deu.gold', model_ger_finetuned), inseq_ger_finetuned, expected=False)

Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 1
Index: 243
This prediction is incorrect
Input -> output (pred): 'Bezug N;NOM;MASC;PL' -> 'Bezuge'
The expected or gold output would be 'Bezüge'


Attributing with input_x_gradient...: 100%|██████████| 8/8 [00:00<00:00, 15.03it/s]




Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 2
Index: 251
This prediction is incorrect
Input -> output (pred): 'Hinterkopf N;NOM;MASC;PL' -> 'Hinterkopfe'
The expected or gold output would be 'Hinterköpfe'


Attributing with input_x_gradient...: 100%|██████████| 13/13 [00:00<00:00, 17.59it/s]




Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 3
Index: 234
This prediction is incorrect
Input -> output (pred): 'Leuchtturm N;NOM;MASC;PL' -> 'Leuchtturme'
The expected or gold output would be 'Leuchttürme'


...

Attributing with input_x_gradient...: 100%|██████████| 10/10 [00:00<00:00, 18.34it/s]




Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 9
Index: 354
This prediction is correct
Input -> output (pred): 'Abenteuer N;NOM;NEUT;PL' -> 'Abenteuer'
The expected or gold output would be 'Abenteuer'


Attributing with input_x_gradient...: 100%|██████████| 11/11 [00:00<00:00, 18.06it/s]




Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 10
Index: 578
This prediction is correct
Input -> output (pred): 'Hauptstraße N;NOM;FEM;PL' -> 'Hauptstraßen'
The expected or gold output would be 'Hauptstraßen'


Attributing with input_x_gradient...: 100%|██████████| 15/15 [00:00<00:00, 18.34it/s]


In [22]:
sample_runner(data_sampler('./data/deu.gold', model_ger_finetuned), inseq_ger_finetuned, expected=True)

Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 1
Index: 243
This prediction is incorrect
Input -> output (gold): 'Bezug N;NOM;MASC;PL' -> 'Bezüge'


Attributing with input_x_gradient...: 100%|██████████| 9/9 [00:00<00:00, 15.58it/s]




Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 2
Index: 251
This prediction is incorrect
Input -> output (gold): 'Hinterkopf N;NOM;MASC;PL' -> 'Hinterköpfe'


Attributing with input_x_gradient...: 100%|██████████| 14/14 [00:00<00:00, 17.71it/s]




Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 3
Index: 234
This prediction is incorrect
Input -> output (gold): 'Leuchtturm N;NOM;MASC;PL' -> 'Leuchttürme'


...

Attributing with input_x_gradient...: 100%|██████████| 10/10 [00:00<00:00, 18.26it/s]




Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 9
Index: 354
This prediction is correct
Input -> output (gold): 'Abenteuer N;NOM;NEUT;PL' -> 'Abenteuer'


Attributing with input_x_gradient...: 100%|██████████| 11/11 [00:00<00:00, 18.18it/s]




Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 10
Index: 578
This prediction is correct
Input -> output (gold): 'Hauptstraße N;NOM;FEM;PL' -> 'Hauptstraßen'


Attributing with input_x_gradient...: 100%|██████████| 15/15 [00:00<00:00, 17.87it/s]


### German From scratch

The sample_runner function splits the given amount of samples in `two` (default is 10) so that `~50% of the samples are samples of correct predictions`, and `~50% of the samples are samples of incorrect predictions`.

First the incorrect predictions are shown, then the correct ones are shown (in the outcomes below, this translates to `5 incorrect items or 1-5, followed by 5 correct items or 6-10`).

In [23]:
sample_runner(data_sampler('./data/deu.gold', model_ger_fromscratch), inseq_ger_fromscratch, expected=False)

Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 1
Index: 209
This prediction is incorrect
Input -> output (pred): 'Ursache N;NOM;FEM;PL' -> 'Frascher'
The expected or gold output would be 'Ursachen'


Attributing with input_x_gradient...: 100%|██████████| 10/10 [00:00<00:00, 23.71it/s]




Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 2
Index: 269
This prediction is incorrect
Input -> output (pred): 'Reibung N;NOM;FEM;PL' -> 'Rebiengungen'
The expected or gold output would be 'Reibungen'


Attributing with input_x_gradient...: 100%|██████████| 14/14 [00:00<00:00, 25.84it/s]




Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 3
Index: 12
This prediction is incorrect
Input -> output (pred): 'Stollen N;NOM;MASC;PL' -> 'Pontel'
The expected or gold output would be 'Stollen'


...

Attributing with input_x_gradient...: 100%|██████████| 8/8 [00:00<00:00, 28.73it/s]




Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 9
Index: 457
This prediction is correct
Input -> output (pred): 'Kescher N;NOM;MASC;PL' -> 'Kescher'
The expected or gold output would be 'Kescher'


Attributing with input_x_gradient...: 100%|██████████| 9/9 [00:00<00:00, 27.61it/s]




Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 10
Index: 74
This prediction is correct
Input -> output (pred): 'Messe N;NOM;FEM;PL' -> 'Messen'
The expected or gold output would be 'Messen'


Attributing with input_x_gradient...: 100%|██████████| 8/8 [00:00<00:00, 26.56it/s]


In [24]:
sample_runner(data_sampler('./data/deu.gold', model_ger_fromscratch), inseq_ger_fromscratch, expected=True)

Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 1
Index: 209
This prediction is incorrect
Input -> output (gold): 'Ursache N;NOM;FEM;PL' -> 'Ursachen'


Attributing with input_x_gradient...: 100%|██████████| 10/10 [00:00<00:00, 23.77it/s]




Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 2
Index: 269
This prediction is incorrect
Input -> output (gold): 'Reibung N;NOM;FEM;PL' -> 'Reibungen'


Attributing with input_x_gradient...: 100%|██████████| 11/11 [00:00<00:00, 26.48it/s]




Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 3
Index: 12
This prediction is incorrect
Input -> output (gold): 'Stollen N;NOM;MASC;PL' -> 'Stollen'


...

Attributing with input_x_gradient...: 100%|██████████| 8/8 [00:00<00:00, 27.74it/s]




Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 9
Index: 457
This prediction is correct
Input -> output (gold): 'Kescher N;NOM;MASC;PL' -> 'Kescher'


Attributing with input_x_gradient...: 100%|██████████| 9/9 [00:00<00:00, 27.23it/s]




Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 10
Index: 74
This prediction is correct
Input -> output (gold): 'Messe N;NOM;FEM;PL' -> 'Messen'


Attributing with input_x_gradient...: 100%|██████████| 8/8 [00:00<00:00, 26.84it/s]


## Turkish

### Setup

In [25]:
model_tur_finetuned = "./models/finetuned_tur"
inseq_tur_finetuned = InseqAttributer(model_tur_finetuned, "input_x_gradient")

In [26]:
model_tur_fromscratch = "./models/saved_model_scratch_tur_new"
inseq_tur_fromscratch = InseqAttributer(model_tur_fromscratch, "input_x_gradient")

### Turkish Finetuned

The sample_runner function splits the given amount of samples in `two` (default is 10) so that `~50% of the samples are samples of correct predictions`, and `~50% of the samples are samples of incorrect predictions`.

First the incorrect predictions are shown, then the correct ones are shown (in the outcomes below, this translates to `5 incorrect items or 1-5, followed by 5 correct items or 6-10`).

In [27]:
sample_runner(data_sampler('./data/tur.gold', model_tur_finetuned, device='cpu'), inseq_tur_finetuned, expected=False)

Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 1
Index: 1066
This prediction is incorrect
Input -> output (pred): 'atılmak V;PFV;DECL;SG;2;NEG;FUT;LGSPEC03' -> 'atılmamış mıydık'
The expected or gold output would be 'atılmış olmayacaksın'


Attributing with input_x_gradient...: 100%|██████████| 23/23 [00:01<00:00, 18.01it/s]




Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 2
Index: 750
This prediction is incorrect
Input -> output (pred): 'katılmak V;OBLIG;SG;3;NEG;PRS;INTR' -> 'katılıyor olmamalı mıydık'
The expected or gold output would be 'katılmameli mi'


Attributing with input_x_gradient...: 100%|██████████| 32/32 [00:01<00:00, 20.22it/s]




Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 3
Index: 242
This prediction is incorrect
Input -> output (pred): 'kimlik N;ABL;SG;PSS1P' -> 'kimlikler mi'
The expected or gold output would be 'kimliğimizden'


...

Attributing with input_x_gradient...: 100%|██████████| 19/19 [00:00<00:00, 18.56it/s]




Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 9
Index: 824
This prediction is correct
Input -> output (pred): 'ilke N;ABL;PL;PSS3S' -> 'ilkelerinden'
The expected or gold output would be 'ilkelerinden'


Attributing with input_x_gradient...: 100%|██████████| 14/14 [00:00<00:00, 20.16it/s]




Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 10
Index: 1564
This prediction is correct
Input -> output (pred): 'seçilmek V;OBLIG;SG;1;NEG;PST;INTR;LGSPEC03' -> 'seçilmemeli miymişim'
The expected or gold output would be 'seçilmemeli miymişim'


Attributing with input_x_gradient...: 100%|██████████| 24/24 [00:01<00:00, 18.83it/s]


In [28]:
sample_runner(data_sampler('./data/tur.gold', model_tur_finetuned, device='cpu'), inseq_tur_finetuned, expected=True)

Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 1
Index: 1066
This prediction is incorrect
Input -> output (gold): 'atılmak V;PFV;DECL;SG;2;NEG;FUT;LGSPEC03' -> 'atılmış olmayacaksın'


Attributing with input_x_gradient...: 100%|██████████| 26/26 [00:01<00:00, 18.62it/s]




Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 2
Index: 750
This prediction is incorrect
Input -> output (gold): 'katılmak V;OBLIG;SG;3;NEG;PRS;INTR' -> 'katılmameli mi'


Attributing with input_x_gradient...: 100%|██████████| 17/17 [00:00<00:00, 19.10it/s]




Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 3
Index: 242
This prediction is incorrect
Input -> output (gold): 'kimlik N;ABL;SG;PSS1P' -> 'kimliğimizden'


...

Attributing with input_x_gradient...: 100%|██████████| 19/19 [00:00<00:00, 19.40it/s]




Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 9
Index: 824
This prediction is correct
Input -> output (gold): 'ilke N;ABL;PL;PSS3S' -> 'ilkelerinden'


Attributing with input_x_gradient...: 100%|██████████| 14/14 [00:00<00:00, 21.43it/s]




Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 10
Index: 1564
This prediction is correct
Input -> output (gold): 'seçilmek V;OBLIG;SG;1;NEG;PST;INTR;LGSPEC03' -> 'seçilmemeli miymişim'


Attributing with input_x_gradient...: 100%|██████████| 24/24 [00:01<00:00, 18.55it/s]


### Turkish From scratch

The sample_runner function splits the given amount of samples in `two` (default is 10) so that `~50% of the samples are samples of correct predictions`, and `~50% of the samples are samples of incorrect predictions`.

First the incorrect predictions are shown, then the correct ones are shown (in the outcomes below, this translates to `5 incorrect items or 1-5, followed by 5 correct items or 6-10`).

In [29]:
sample_runner(data_sampler('./data/tur.gold', model_tur_fromscratch, device='cpu'), inseq_tur_fromscratch, expected=False)

Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 1
Index: 1456
This prediction is incorrect
Input -> output (pred): 'dindar ADJ;PL;2;POS;PST;INTR;LGSPEC01' -> 'dadarandi dir miymişiz'
The expected or gold output would be 'dindar mıydınız?'


Attributing with input_x_gradient...: 100%|██████████| 25/25 [00:00<00:00, 28.27it/s]




Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 2
Index: 1552
This prediction is incorrect
Input -> output (pred): 'kızmak V;DECL;SG;2;NEG;PST;LGSPEC01;LGSPEC03' -> 'kızmamıştım'
The expected or gold output would be 'kızmamışmışsın'


Attributing with input_x_gradient...: 100%|██████████| 17/17 [00:00<00:00, 29.07it/s]




Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 3
Index: 883
This prediction is incorrect
Input -> output (pred): 'şaşılmak V;HAB;DECL;IND;PL;2;POS;PST' -> 'şaklaşırdınız'
The expected or gold output would be 'şaşılırdınız'


...

Attributing with input_x_gradient...: 100%|██████████| 37/37 [00:01<00:00, 30.44it/s]




Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 9
Index: 1956
This prediction is correct
Input -> output (pred): 'dövüşmek V;PFV;DECL;SG;1;NEG;FUT;LGSPEC03' -> 'dövüşmüş olmayacağım'
The expected or gold output would be 'dövüşmüş olmayacağım'


Attributing with input_x_gradient...: 100%|██████████| 29/29 [00:00<00:00, 29.06it/s]




Testing Predicted (pred) outcome (what did the model take from the input during generation)
Sample: 10
Index: 1540
This prediction is correct
Input -> output (pred): 'katılaşmak V;DECL;IND;SG;3;NEG;PST' -> 'katılaşmadı'
The expected or gold output would be 'katılaşmadı'


Attributing with input_x_gradient...: 100%|██████████| 16/16 [00:00<00:00, 30.25it/s]


In [30]:
sample_runner(data_sampler('./data/tur.gold', model_tur_fromscratch, device='cpu'), inseq_tur_fromscratch, expected=True)

Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 1
Index: 1456
This prediction is incorrect
Input -> output (gold): 'dindar ADJ;PL;2;POS;PST;INTR;LGSPEC01' -> 'dindar mıydınız?'


Attributing with input_x_gradient...: 100%|██████████| 21/21 [00:00<00:00, 29.91it/s]




Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 2
Index: 1552
This prediction is incorrect
Input -> output (gold): 'kızmak V;DECL;SG;2;NEG;PST;LGSPEC01;LGSPEC03' -> 'kızmamışmışsın'


Attributing with input_x_gradient...: 100%|██████████| 22/22 [00:00<00:00, 30.48it/s]




Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 3
Index: 883
This prediction is incorrect
Input -> output (gold): 'şaşılmak V;HAB;DECL;IND;PL;2;POS;PST' -> 'şaşılırdınız'


...

Attributing with input_x_gradient...: 100%|██████████| 37/37 [00:01<00:00, 25.89it/s]




Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 9
Index: 1956
This prediction is correct
Input -> output (gold): 'dövüşmek V;PFV;DECL;SG;1;NEG;FUT;LGSPEC03' -> 'dövüşmüş olmayacağım'


Attributing with input_x_gradient...: 100%|██████████| 29/29 [00:01<00:00, 26.55it/s]




Testing Expected (gold) outcome (what would the model look at to get to the expected outcome)
Sample: 10
Index: 1540
This prediction is correct
Input -> output (gold): 'katılaşmak V;DECL;IND;SG;3;NEG;PST' -> 'katılaşmadı'


Attributing with input_x_gradient...: 100%|██████████| 16/16 [00:00<00:00, 26.56it/s]
